In [1]:
import geopandas as gpd
import pandas as pd
import plotly.express as px
from shapely.geometry import Point
from sklearn.preprocessing import MinMaxScaler
from os.path import exists
from urllib.request import urlretrieve
import os

# Ensure the 'data' directory exists
if not os.path.exists('data'):
    os.makedirs('data')

# Function to fetch data
def fetch_data(file_path, url):
    if not exists(file_path):
        urlretrieve(url, file_path)
    return file_path

# Function to get GeoDataFrame from WFS
def get_gdf_from_wfs(layer):
    file_path = f'data/{layer}.json'
    url = f"https://data.wien.gv.at/daten/geo?service=WFS&request=GetFeature&version=1.1.0&typeName=ogdwien:{layer}&srsName=EPSG:4326&outputFormat=json"
    fetch_data(file_path, url)
    return gpd.read_file(file_path)

# Function to get heat vulnerability index DataFrame
def get_heatvulnerabilityindex_df():
    file = 'data/heatvulnerabilityindex.csv'
    url = 'https://www.wien.gv.at/gogv/l9ogdaverageurbanheatvulnerabilityindex'
    fetch_data(file, url)
    df = pd.read_csv(file, sep=';', encoding='latin1', decimal=',')
    df.set_index('SUB_DISTRICT_CODE_VIE', inplace=True)
    return df

# Function to get heat vulnerability index GeoDataFrame
def get_heatvulnerabilityindex_gdf():
    df = get_heatvulnerabilityindex_df()
    districts = get_gdf_from_wfs('ZAEHLBEZIRKOGD')
    districts['SUB_DISTRICT_CODE_VIE'] = districts['ZBEZ'].astype(int) + 90000
    districts.set_index('SUB_DISTRICT_CODE_VIE', inplace=True)
    gdf = districts.join(df) 
    return gdf

# Function to normalize series
def normalize_series(series):
    scaler = MinMaxScaler()
    return scaler.fit_transform(series.values.reshape(-1, 1)).flatten()

# Function to find nearest point
def find_nearest(gdf, point):
    return gdf.geometry.distance(point).idxmin()

# Process data
def process_data():
    # Load data
    heat_vulnerability_gdf = get_heatvulnerabilityindex_gdf()
    dog_amenities_gdf = get_gdf_from_wfs('HUNDESACKERLOGD')
    swimming_pools_gdf = get_gdf_from_wfs('SCHWIMMBADOGD')
    
    # Ensure all GeoDataFrames are in the same CRS
    dog_amenities_gdf = dog_amenities_gdf.to_crs(heat_vulnerability_gdf.crs)
    swimming_pools_gdf = swimming_pools_gdf.to_crs(heat_vulnerability_gdf.crs)
    
    # Find centroids of heat vulnerability areas
    heat_vulnerability_gdf['centroid'] = heat_vulnerability_gdf.geometry.to_crs(epsg=31256).centroid.to_crs(epsg=4326)
    
    # Calculate proximity to dog amenities and swimming pools
    dog_density = []
    swimming_proximity = []

    for centroid in heat_vulnerability_gdf['centroid']:
        dog_density.append(dog_amenities_gdf.geometry.distance(centroid).min())
        swimming_proximity.append(swimming_pools_gdf.geometry.distance(centroid).min())
    
    heat_vulnerability_gdf['dog_density'] = normalize_series(pd.Series(dog_density))
    heat_vulnerability_gdf['swimming_proximity'] = normalize_series(-pd.Series(swimming_proximity))  # Inverted to make closer pools higher score
    
    # Composite score
    heat_vulnerability_gdf['composite_score'] = (normalize_series(-heat_vulnerability_gdf['AVG_UHVI_A']) + 
                                                 heat_vulnerability_gdf['dog_density'] + 
                                                 heat_vulnerability_gdf['swimming_proximity']) / 3

    return heat_vulnerability_gdf, dog_amenities_gdf, swimming_pools_gdf

# Plotting function
def plot_data(heat_vulnerability_gdf):
    fig = px.choropleth_mapbox(
        heat_vulnerability_gdf,
        geojson=heat_vulnerability_gdf.geometry,
        locations=heat_vulnerability_gdf.index,
        color='composite_score',
        color_continuous_scale="RdYlGn",
        mapbox_style="open-street-map",
        zoom=10,
        center={"lat": 48.2082, "lon": 16.3738},
        opacity=0.6,
        labels={'composite_score': 'Composite Score'},
        title="Optimal Zones in Vienna for People Who Hate the Heat, Have a Dog, and Like Swimming",
        hover_data={'NAME_VIE': True}  # Add NAME_VIE for hover information
    )

    fig.update_layout(
        margin={"r":0,"t":50,"l":0,"b":0},
        height=700,  # Adjust height to make it more square
        legend_title_text="Composite Score"
    )
    
    fig.update_traces(marker_line_width=0.5, marker_line_color='white')
    
    fig.update_geos(fitbounds="locations", visible=False)
    
    fig.show()

# Execute
heat_vulnerability_gdf, dog_amenities_gdf, swimming_pools_gdf = process_data()
plot_data(heat_vulnerability_gdf)


C:\Users\jer93\AppData\Local\Temp\ipykernel_11204\3746776355.py:73: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  dog_density.append(dog_amenities_gdf.geometry.distance(centroid).min())
C:\Users\jer93\AppData\Local\Temp\ipykernel_11204\3746776355.py:74: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  swimming_proximity.append(swimming_pools_gdf.geometry.distance(centroid).min())
